In [167]:
import numpy as np
import pandas as pd
import statistics
import os
from dotenv import load_dotenv
load_dotenv()
import urllib.parse
import requests


A continuación abrimos el dataset descargado de kaggle.

In [168]:
df = pd.read_csv("Data_Source/filmtv_movies - ENG.csv")

Nos quedamos con las columnas que son interesantes para nosotros.

In [171]:
Film_df =df[["filmtv_id","title","year","genre","director"]]

Hacemos drop de los Nan values

In [173]:
missing_values= (Film_df.isnull().sum()/Film_df.shape[0]).sort_values(ascending=False).head(10)
missing_values             

genre               0.003795
director_dataset    0.001196
year                0.000224
title               0.000000
filmtv_id           0.000000
dtype: float64

In [174]:
def drop_null(table,subset):
    table.dropna(subset=[f"{subset}"],inplace=True)

In [175]:
drop_null(Film_df,"director_dataset")
drop_null(Film_df,"year")
drop_null(Film_df,"genre")



Comprobamos el % de valores null despues de limpiar los datos.

In [176]:
missing_values= (Film_df.isnull().sum()/Film_df.shape[0]).sort_values(ascending=False).head(10)
missing_values   

director_dataset    0.0
genre               0.0
year                0.0
title               0.0
filmtv_id           0.0
dtype: float64

Convertimos el año en una variable tipo int. 

In [177]:
Film_df.year = Film_df.year.astype(int)

In [178]:
Film_df

filmtv_id                                        title  year  \
0              2  Bugs Bunny's Third Movie: 1001 Rabbit Tales  1982   
1              3                    18 anni tra una settimana  1991   
2             17                             Ride a Wild Pony  1976   
3             18                                        Diner  1982   
4             20              A che servono questi quattrini?  1942   
...          ...                                          ...   ...   
53492     179865                        Psycho Brother In-Law  2017   
53493     179885                        Il berretto a sonagli  1981   
53494     179887                                 Put lubenica  2006   
53495     179919                            Più forte sorelle  1973   
53496     179937           Henry Danger: Henry & the Bad Girl  2015   

           genre                      director_dataset  
0      Animation  David Detiege, Art Davis, Bill Perez  
1          Drama                         Luigi Perelli  
2       Romantic                           Don Chaffey  
3         Comedy                        Barry Levinson  
4         Comedy                        Esodo Pratelli  
...          ...                                   ...  
53492   Thriller                       Jose Montesinos  
53493     Comedy                    Eduardo De Filippo  
53494      Drama                        Branko Schmidt  
53495    Western         Mario Bianchi, Renzo Girolami  
53496     Comedy                          Steve Hoefer  

[53222 rows x 5 columns]

In [ ]:
Creamos una función que nos servira para más adelante sobrescribir los datos con los de la API.  

In [179]:
def actualiza_valor_fila(tabla,fila_valor,fila,columna,valor):
    tabla.loc[tabla[f"{fila_valor}"]== fila,columna]= valor

Hacemos una primera prueba de la api.

In [182]:
def getFromGithub():
    url = "https://api.themoviedb.org/3/search/movie?api_key=c734ee865c6f0e6e56f5f18ae5d63c73&language=en-US&query=Ride%20a%20Wild%20Pony&page=1&include_adult=false"
    res = requests.get(url)
    print(res.url)
    return res.json()

Y obtenemos el siguiente resultado.

In [183]:
getFromGithub()

https://api.themoviedb.org/3/search/movie?api_key=c734ee865c6f0e6e56f5f18ae5d63c73&language=en-US&query=Ride%20a%20Wild%20Pony&page=1&include_adult=false


{'page': 1,
 'total_results': 1,
 'total_pages': 1,
 'results': [{'popularity': 2.187,
   'id': 103765,
   'video': False,
   'vote_count': 6,
   'vote_average': 6.4,
   'title': 'Ride a Wild Pony',
   'release_date': '1975-11-02',
   'original_language': 'en',
   'original_title': 'Ride a Wild Pony',
   'genre_ids': [12],
   'backdrop_path': '/i4E8gtvy4vHL3QDnk3m9VuJR7dr.jpg',
   'adult': False,
   'overview': "Scott, a poor farm boy, is given a wild pony from a wealthy ranch owner's herd to ride to and from school. Scott and his pony soon become an inseparable team, until one day the pony suddenly disappears. Soon after, the ranch owner's handicapped daughter Josie has a wild pony especially trained to pull her cart. But Scott is convinced that Josie's pony is actually his, which leads to a court battle that divides their small Australian town. One child must ultimately lose the pony when true ownership is decided.",
   'poster_path': '/w2il8FdXIzKhiGvjSrJ5mp37yK2.jpg'}]}

In [184]:
prueba1 = pd.DataFrame()

Creamos una funcuón que nos servira para buscar porteriormente en el loop.

In [ ]:
def busca(key,film_name):
    url = "https://api.themoviedb.org/3/search/movie?api_key="+key+"&language=en-US&query="+film_name
    res = requests.get(url)
    print(url)
    return res.json()
    

Creamos una columna nueva para luego sobrescribir con la función que hemos creado anteriormente

In [193]:
Film_df["popularity"]=""

Creamos un bucle para obtener de la api 

In [ ]:
for i in Film_df["title"]:
    try:
        prueba1= busca(apiKey,urllib.parse.quote(f"{i}"))
        popularity= prueba1["results"][0]["popularity"]
        print(popularity)
        actualiza_valor_fila(Film_df,"title",i,"popularity",popularity)
    except:
        actualiza_valor_fila(Film_df,"title",i,"popularity",None)
        
    
    
    

https://api.themoviedb.org/3/search/movie?api_key=c734ee865c6f0e6e56f5f18ae5d63c73&language=en-US&query=18%20anni%20tra%20una%20settimana
1.4
https://api.themoviedb.org/3/search/movie?api_key=c734ee865c6f0e6e56f5f18ae5d63c73&language=en-US&query=Ride%20a%20Wild%20Pony
3.062
https://api.themoviedb.org/3/search/movie?api_key=c734ee865c6f0e6e56f5f18ae5d63c73&language=en-US&query=Diner
10.664
https://api.themoviedb.org/3/search/movie?api_key=c734ee865c6f0e6e56f5f18ae5d63c73&language=en-US&query=A%20che%20servono%20questi%20quattrini%3F
0.628
https://api.themoviedb.org/3/search/movie?api_key=c734ee865c6f0e6e56f5f18ae5d63c73&language=en-US&query=A%20ciascuno%20il%20suo
5.421
https://api.themoviedb.org/3/search/movie?api_key=c734ee865c6f0e6e56f5f18ae5d63c73&language=en-US&query=Dead-Bang
6.754
https://api.themoviedb.org/3/search/movie?api_key=c734ee865c6f0e6e56f5f18ae5d63c73&language=en-US&query=A...%20come%20assassino
1.463
https://api.themoviedb.org/3/search/movie?api_key=c734ee865c6f0e6e56

https://api.themoviedb.org/3/search/movie?api_key=c734ee865c6f0e6e56f5f18ae5d63c73&language=en-US&query=Water
16.631
https://api.themoviedb.org/3/search/movie?api_key=c734ee865c6f0e6e56f5f18ae5d63c73&language=en-US&query=Acque%20di%20primavera
3.855
https://api.themoviedb.org/3/search/movie?api_key=c734ee865c6f0e6e56f5f18ae5d63c73&language=en-US&query=Action%20Jackson
13.23
https://api.themoviedb.org/3/search/movie?api_key=c734ee865c6f0e6e56f5f18ae5d63c73&language=en-US&query=Shi%20no%20Toge
3.07
https://api.themoviedb.org/3/search/movie?api_key=c734ee865c6f0e6e56f5f18ae5d63c73&language=en-US&query=East%20of%20Elephant%20Rock
1.456
https://api.themoviedb.org/3/search/movie?api_key=c734ee865c6f0e6e56f5f18ae5d63c73&language=en-US&query=Mail%20Order%20Bride
3.885
https://api.themoviedb.org/3/search/movie?api_key=c734ee865c6f0e6e56f5f18ae5d63c73&language=en-US&query=Ad%20Ovest%20di%20Paperino
3.984
https://api.themoviedb.org/3/search/movie?api_key=c734ee865c6f0e6e56f5f18ae5d63c73&language=

https://api.themoviedb.org/3/search/movie?api_key=c734ee865c6f0e6e56f5f18ae5d63c73&language=en-US&query=Agguato%20a%20Tangeri
0.6
https://api.themoviedb.org/3/search/movie?api_key=c734ee865c6f0e6e56f5f18ae5d63c73&language=en-US&query=Across%20the%20Pacific
5.307
https://api.themoviedb.org/3/search/movie?api_key=c734ee865c6f0e6e56f5f18ae5d63c73&language=en-US&query=Hard%20Ticket%20to%20Hawaii
6.633
https://api.themoviedb.org/3/search/movie?api_key=c734ee865c6f0e6e56f5f18ae5d63c73&language=en-US&query=Hostile%20Guns
2.715
https://api.themoviedb.org/3/search/movie?api_key=c734ee865c6f0e6e56f5f18ae5d63c73&language=en-US&query=Rhino%21
8.823
https://api.themoviedb.org/3/search/movie?api_key=c734ee865c6f0e6e56f5f18ae5d63c73&language=en-US&query=Die%20Flusspiraten%20vom%20Mississippi
1.53
https://api.themoviedb.org/3/search/movie?api_key=c734ee865c6f0e6e56f5f18ae5d63c73&language=en-US&query=Agi%20Murad%2C%20il%20diavolo%20bianco
3.121
https://api.themoviedb.org/3/search/movie?api_key=c734ee86

https://api.themoviedb.org/3/search/movie?api_key=c734ee865c6f0e6e56f5f18ae5d63c73&language=en-US&query=Run%20for%20Cover
4.286
https://api.themoviedb.org/3/search/movie?api_key=c734ee865c6f0e6e56f5f18ae5d63c73&language=en-US&query=Anthony%20and%20Cleopatra
1.336
https://api.themoviedb.org/3/search/movie?api_key=c734ee865c6f0e6e56f5f18ae5d63c73&language=en-US&query=A%20l%27ombre%20d%27un%20%C3%A9t%C3%A9
0.6
https://api.themoviedb.org/3/search/movie?api_key=c734ee865c6f0e6e56f5f18ae5d63c73&language=en-US&query=Breathless
9.682
https://api.themoviedb.org/3/search/movie?api_key=c734ee865c6f0e6e56f5f18ae5d63c73&language=en-US&query=All%27ultimo%20sangue
3.915
https://api.themoviedb.org/3/search/movie?api_key=c734ee865c6f0e6e56f5f18ae5d63c73&language=en-US&query=One%20A.M.
6.127
https://api.themoviedb.org/3/search/movie?api_key=c734ee865c6f0e6e56f5f18ae5d63c73&language=en-US&query=Cutter%27s%20Way
7.308
https://api.themoviedb.org/3/search/movie?api_key=c734ee865c6f0e6e56f5f18ae5d63c73&langu

https://api.themoviedb.org/3/search/movie?api_key=c734ee865c6f0e6e56f5f18ae5d63c73&language=en-US&query=Come%20and%20Get%20It
3.64
https://api.themoviedb.org/3/search/movie?api_key=c734ee865c6f0e6e56f5f18ae5d63c73&language=en-US&query=The%20Ploughman%27s%20Lunch
2.614
https://api.themoviedb.org/3/search/movie?api_key=c734ee865c6f0e6e56f5f18ae5d63c73&language=en-US&query=Forever%20Amber
3.802
https://api.themoviedb.org/3/search/movie?api_key=c734ee865c6f0e6e56f5f18ae5d63c73&language=en-US&query=Boxcar%20Bertha
10.719
https://api.themoviedb.org/3/search/movie?api_key=c734ee865c6f0e6e56f5f18ae5d63c73&language=en-US&query=Private%20School
9.792
https://api.themoviedb.org/3/search/movie?api_key=c734ee865c6f0e6e56f5f18ae5d63c73&language=en-US&query=American%20Eagle
1.723
https://api.themoviedb.org/3/search/movie?api_key=c734ee865c6f0e6e56f5f18ae5d63c73&language=en-US&query=American%20Fever
1.4
https://api.themoviedb.org/3/search/movie?api_key=c734ee865c6f0e6e56f5f18ae5d63c73&language=en-US&q

...

https://api.themoviedb.org/3/search/movie?api_key=c734ee865c6f0e6e56f5f18ae5d63c73&language=en-US&query=Hailey%20Dean%20Mystery%3A%20Deadly%20Estate
5.549
https://api.themoviedb.org/3/search/movie?api_key=c734ee865c6f0e6e56f5f18ae5d63c73&language=en-US&query=Hailey%20Dean%20Mystery%3A%20Murder%2C%20with%20Love
5.758
https://api.themoviedb.org/3/search/movie?api_key=c734ee865c6f0e6e56f5f18ae5d63c73&language=en-US&query=Rosamunde%20Pilcher%3A%20Erdbeeren%20im%20Fr%C3%BChling
1.258
https://api.themoviedb.org/3/search/movie?api_key=c734ee865c6f0e6e56f5f18ae5d63c73&language=en-US&query=Meurtres%20%C3%A0...%3A%20La%20disparue%20du%20Pyla
https://api.themoviedb.org/3/search/movie?api_key=c734ee865c6f0e6e56f5f18ae5d63c73&language=en-US&query=Scooby-Doo%21%20and%20WWE%3A%20Curse%20of%20the%20Speed%20Demon
13.246
https://api.themoviedb.org/3/search/movie?api_key=c734ee865c6f0e6e56f5f18ae5d63c73&language=en-US&query=The%20Eternal%20Sea
1.4
https://api.themoviedb.org/3/search/movie?api_key=c734ee8

https://api.themoviedb.org/3/search/movie?api_key=c734ee865c6f0e6e56f5f18ae5d63c73&language=en-US&query=Caniba
2.65
https://api.themoviedb.org/3/search/movie?api_key=c734ee865c6f0e6e56f5f18ae5d63c73&language=en-US&query=Piazza%20Vittorio
0.6
https://api.themoviedb.org/3/search/movie?api_key=c734ee865c6f0e6e56f5f18ae5d63c73&language=en-US&query=La%20lucida%20follia%20di%20Marco%20Ferreri
0.932
https://api.themoviedb.org/3/search/movie?api_key=c734ee865c6f0e6e56f5f18ae5d63c73&language=en-US&query=Barbiana%20%2765%20-%20La%20lezione%20di%20Don%20Milani
0.6
https://api.themoviedb.org/3/search/movie?api_key=c734ee865c6f0e6e56f5f18ae5d63c73&language=en-US&query=Napadid%20shodan
0.6
https://api.themoviedb.org/3/search/movie?api_key=c734ee865c6f0e6e56f5f18ae5d63c73&language=en-US&query=The%20Rape%20of%20Recy%20Taylor
4.864
https://api.themoviedb.org/3/search/movie?api_key=c734ee865c6f0e6e56f5f18ae5d63c73&language=en-US&query=Ha%20ben%20dod
https://api.themoviedb.org/3/search/movie?api_key=c734

https://api.themoviedb.org/3/search/movie?api_key=c734ee865c6f0e6e56f5f18ae5d63c73&language=en-US&query=La%20llamada
9.854
https://api.themoviedb.org/3/search/movie?api_key=c734ee865c6f0e6e56f5f18ae5d63c73&language=en-US&query=Les%20Estivants
4.623
https://api.themoviedb.org/3/search/movie?api_key=c734ee865c6f0e6e56f5f18ae5d63c73&language=en-US&query=Karla
8.009
https://api.themoviedb.org/3/search/movie?api_key=c734ee865c6f0e6e56f5f18ae5d63c73&language=en-US&query=Panny%20z%20Wilka
4.535
https://api.themoviedb.org/3/search/movie?api_key=c734ee865c6f0e6e56f5f18ae5d63c73&language=en-US&query=Death%20Wish
23.105
https://api.themoviedb.org/3/search/movie?api_key=c734ee865c6f0e6e56f5f18ae5d63c73&language=en-US&query=Rocco%20Chinnici%20-%20%C3%88%20cos%C3%AC%20lieve%20il%20tuo%20bacio%20sulla%20fronte
0.972
https://api.themoviedb.org/3/search/movie?api_key=c734ee865c6f0e6e56f5f18ae5d63c73&language=en-US&query=Koudelka%20Shooting%20Holy%20Land
0.619
https://api.themoviedb.org/3/search/movie?a

https://api.themoviedb.org/3/search/movie?api_key=c734ee865c6f0e6e56f5f18ae5d63c73&language=en-US&query=FANatic
10.758
https://api.themoviedb.org/3/search/movie?api_key=c734ee865c6f0e6e56f5f18ae5d63c73&language=en-US&query=Innamorati%20di%20me
0.6
https://api.themoviedb.org/3/search/movie?api_key=c734ee865c6f0e6e56f5f18ae5d63c73&language=en-US&query=Viel%20L%C3%A4rm%20um%20Nick
https://api.themoviedb.org/3/search/movie?api_key=c734ee865c6f0e6e56f5f18ae5d63c73&language=en-US&query=Wetlands
3.869
https://api.themoviedb.org/3/search/movie?api_key=c734ee865c6f0e6e56f5f18ae5d63c73&language=en-US&query=Summer%20in%20the%20City
5.693
https://api.themoviedb.org/3/search/movie?api_key=c734ee865c6f0e6e56f5f18ae5d63c73&language=en-US&query=Recipe%20for%20Love
8.597
https://api.themoviedb.org/3/search/movie?api_key=c734ee865c6f0e6e56f5f18ae5d63c73&language=en-US&query=Looking%20for%20Mr.%20Right
4.692
https://api.themoviedb.org/3/search/movie?api_key=c734ee865c6f0e6e56f5f18ae5d63c73&language=en-US

https://api.themoviedb.org/3/search/movie?api_key=c734ee865c6f0e6e56f5f18ae5d63c73&language=en-US&query=Lilly%20Sch%C3%B6nauer%3A%20Verliebt%20in%20einen%20Unbekannten
0.763
https://api.themoviedb.org/3/search/movie?api_key=c734ee865c6f0e6e56f5f18ae5d63c73&language=en-US&query=Charm%C3%B8ren
1.822
https://api.themoviedb.org/3/search/movie?api_key=c734ee865c6f0e6e56f5f18ae5d63c73&language=en-US&query=Katie%20Fforde%3A%20Zur%C3%BCck%20ans%20Meer
0.944
https://api.themoviedb.org/3/search/movie?api_key=c734ee865c6f0e6e56f5f18ae5d63c73&language=en-US&query=Secrets%20of%20Eden
5.094
https://api.themoviedb.org/3/search/movie?api_key=c734ee865c6f0e6e56f5f18ae5d63c73&language=en-US&query=A%20Mother%27s%20Nightmare
6.843
https://api.themoviedb.org/3/search/movie?api_key=c734ee865c6f0e6e56f5f18ae5d63c73&language=en-US&query=Killer%20Coach
3.111
https://api.themoviedb.org/3/search/movie?api_key=c734ee865c6f0e6e56f5f18ae5d63c73&language=en-US&query=Cupid%2C%20Inc.
4.605
https://api.themoviedb.org/3

Comprobamos cuantos null tenemos.

In [261]:
with pd.option_context('display.max_rows', None, 'display.max_columns', None):
    print(prueba_Film_df.popularity.value_counts())

NA        72
1.4       44
0.6       17
0.841      3
1.126      3
0.84       3
14.803     3
1.091      3
1.371      2
0.628      2
5.101      2
3.506      2
1.135      2
2.934      2
1.45       2
4.159      2
38.28      2
0.921      2
5.122      2
8.889      2
1.487      2
5.814      2
2.004      2
3.64       2
1.544      2
2.469      2
0.877      2
3.004      2
3.121      2
1.47       2
2.979      2
2.639      2
1.806      2
0.654      2
9.512      2
6.275      2
12.305     2
4.439      2
0.982      2
0.627      2
3.862      2
5.67       2
2.744      2
6.033      1
5.831      1
9.47       1
9.201      1
3.545      1
1.53       1
1.68       1
9.702      1
4.933      1
18.176     1
10.769     1
4.108      1
3.022      1
11.388     1
4.552      1
7.469      1
5.451      1
2.969      1
8.686      1
1.722      1
15.76      1
13.986     1
5.423      1
14.016     1
11.494     1
7.944      1
4.555      1
5.29       1
3.566      1
1.172      1
12.888     1
6.813      1
4.115      1
8.766      1

Eliminamos aquellas celdas que no obtenemos resultado desde la API.

In [ ]:
drop_null(Film_df,"popularity")

In [265]:
with pd.option_context('display.max_rows', None, 'display.max_columns', None):
    print(prueba_Film_df.popularity.value_counts())

1.400     44
0.600     17
1.126      3
0.841      3
0.840      3
14.803     3
1.091      3
0.921      2
1.371      2
0.877      2
3.121      2
0.654      2
38.280     2
3.506      2
1.544      2
5.122      2
9.512      2
5.670      2
5.814      2
3.640      2
2.744      2
4.159      2
0.628      2
2.934      2
1.487      2
8.889      2
12.305     2
0.627      2
1.135      2
1.450      2
3.004      2
5.101      2
4.439      2
6.275      2
2.639      2
1.470      2
1.806      2
2.004      2
0.982      2
2.979      2
2.469      2
3.862      2
10.769     1
8.749      1
5.831      1
4.555      1
4.933      1
7.469      1
9.702      1
8.683      1
9.571      1
3.545      1
1.680      1
8.766      1
5.451      1
18.176     1
1.969      1
13.210     1
4.108      1
2.612      1
1.172      1
12.888     1
11.332     1
14.016     1
5.423      1
15.760     1
6.701      1
6.944      1
4.984      1
11.388     1
3.022      1
1.722      1
8.686      1
5.037      1
3.575      1
3.986      1
4.938      1

In [292]:
Film_df_remaned = Film_df.rename(columns={'filmtv_id':'ID_Pelicula',
                                   'title':'titulo','year':'año','genre':'genero','director_dataset':'director','popularity':'popularidad'})

Finalmente exportamos el csv para su posterior uso.

In [296]:
drop_null(Film_df_remaned,"popularidad")

In [298]:
Film_df_remaned.to_csv('Conpopularity1.csv', index=False)

In [302]:
import os
from dotenv import load_dotenv
load_dotenv()

apiKey = os.getenv("ap_film")

In [303]:
print(apiKey)

c734ee865c6f0e6e56f5f18ae5d63c73
